In [1]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.decomposition import PCA
from imblearn.under_sampling import RandomUnderSampler
from loguru import logger
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from imblearn.under_sampling import RandomUnderSampler
from pandas.api.types import is_numeric_dtype
from itertools import product



In [2]:
DROP_COLS = ['trip_stages',  'trip_duration', 'dem_population_18','dem_population_65','den_perc_hotel','den_perc_religious','den_perc_infra','des_total_length','des_degree','des_closeness','des_eigenvector']
ID_COLS =  ['id_municipality','id_taz','elevator','id_household','id_person','id_trip'] 
CONTROLS = ['trip_purpose','trip_distance','des_age_range','den_quartile','dem_cohort','dem_hou_structure']
CATEGORICAL = ['dem_activity','dem_hou_structure', 'dem_att_nopublic','dem_att_noprivate']
EXCLUDE = DROP_COLS+ID_COLS+CONTROLS+CATEGORICAL

def prepare_data(path):

    or_data = {}
    scaler = StandardScaler()
    encoder = OneHotEncoder(drop='first', sparse_output=False)

    for dft in ('900','1200','1500'):
        or_data.update({dft: pd.read_parquet(path.format(di = dft))})

    for d, dft in or_data.items():
        dft = dft[dft['trip_mode'].isin(['Motor - Personal','Walking'])]
        dft.drop(columns=DROP_COLS, inplace=True)
        dft.rename(
        columns={
            w:w.replace("dens_","den_") for w in ['dens_pop_total','dens_hou_total', 'dens_far', 'dens_far_ag', 'den_perc_unbuilt','dens_built_total']},
            inplace = True)
        dft = dft[dft['trip_distance'] <= int(d)/1000]
        dft.set_index('id',inplace=True)
        
        DEMOGRAPHIC = [c for c in dft if c.startswith('dem_') and is_numeric_dtype(dft[c]) and not c in EXCLUDE]
        DENSITY = [c for c in dft if c.startswith('den_') and is_numeric_dtype(dft[c]) and not c in EXCLUDE]
        DESIGN = [c for c in dft if c.startswith('des_') and is_numeric_dtype(dft[c]) and not c in EXCLUDE]
        DIVERSITY = [c for c in dft if c.startswith('div_') and is_numeric_dtype(dft[c]) and not c in EXCLUDE]
        ACCESSIBILITY = [c for c in dft if c.startswith('acc_') and is_numeric_dtype(dft[c]) and not c in EXCLUDE]

        numerical_features = DEMOGRAPHIC+DENSITY+DESIGN+DIVERSITY+ACCESSIBILITY
        print(numerical_features)

        dft[numerical_features] = dft[numerical_features].fillna(0)
        dft[numerical_features] = scaler.fit_transform(dft[numerical_features])
        dft.drop(columns=['tz_id'],inplace=True)
        dft['dem_education'] = dft['dem_education'].map({'Second - B':3, 'Second - A':2, 'First':1, 'No':0, 'Third':4})
        dft['dem_activity'] = dft['dem_activity'].map({'Retired':'retired', 'Student':'student', 'Caretaker':'caretaker', 'Worker':'worker', 'Unemployed':'unemployed'})
        dft['dem_att_noprivate'] = dft['dem_att_noprivate'].map(
        {'Other':'other','Less Convenient':'lessconvenient','Hard to Park':'hardtopark','Takes Longer':'takeslonger','Dislike':'dislike','Congestion':'congestion'})
        dft['dem_att_nopublic'] = dft['dem_att_nopublic'].map(
            {'Prefer Active Modes':'preferactive',
            'Takes Longer':'takeslonger',
            'Very Close':'veryclose',
            'Bad Service':'badservice',
            'Other':'other',
            'Less Convenient':'lessconvenient'})
        dft['dem_gender'] = dft['dem_gender'].map({'Male':1,'Female':0})
        dft['dem_att_license'] = dft['dem_att_license'].map({'Yes':1,'No':0})
        dft['dem_att_card'] = dft['dem_att_card'].map({'Yes':1,'No':0})
        dft['dem_att_vehicle'] = dft['dem_att_vehicle'].map({'Yes':1,'No':0})
        dft['dem_hou_structure'] = dft['dem_hou_structure'].map(
        {'Students (Age 13–18)':'students_age13_18', 'Retirees':'retiree', 'Students (Age 6–12)':'students_age6_12',
       'Full-Time Workers':'worker', 'Other':'other', 'Students (age 19+)':'age19m', 'Children':'children'}
        )

        
        encoded_features = pd.DataFrame(encoder.fit_transform(dft[CATEGORICAL]), 
                                    columns=encoder.get_feature_names_out(CATEGORICAL),index=dft.index)
        
        dft = pd.concat([dft, encoded_features], axis = 1)
        dft = dft.drop(columns=[c for c in CATEGORICAL if c!='dem_hou_structure'])
        or_data.update({d:dft})

    return or_data


In [3]:
path = r"G:\Mi unidad\walknet_datalake\extractions\extraction_{di}.parquet"
original_data = prepare_data(path)

C:\Users\katul\AppData\Local\Temp\ipykernel_12728\855449977.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dft.drop(columns=DROP_COLS, inplace=True)
C:\Users\katul\AppData\Local\Temp\ipykernel_12728\855449977.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dft.rename(
C:\Users\katul\AppData\Local\Temp\ipykernel_12728\855449977.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dft.drop(columns=DROP_COLS, inplace=True)
C:\U

['dem_age', 'dem_hou_size', 'dem_hou_trips', 'dem_income', 'dem_household_size', 'dem_mean_age', 'den_pop_total', 'den_hou_total', 'den_far', 'den_far_ag', 'den_perc_unbuilt', 'den_built_total', 'den_perc_housing_sfr', 'den_perc_housing_ch', 'den_perc_care_other', 'den_perc_care_public', 'den_perc_school_superior', 'den_perc_school_basic', 'den_perc_leisure_bar', 'den_perc_leisure_cultural', 'den_perc_leisure_shows', 'den_perc_shopping_mall', 'den_perc_shopping_market', 'den_perc_shopping_alone', 'den_perc_sport_other', 'den_perc_office', 'den_perc_industrial', 'den_perc_storage', 'den_perc_parking', 'des_mean_degree', 'des_straightness', 'des_block_length', 'des_culdesac', 'des_slope', 'des_building_age', 'des_betweenness', 'div_wt_care', 'div_ut_care', 'div_wt_school', 'div_ut_school', 'div_wt_leisure', 'div_ut_leisure', 'div_wt_shopping', 'div_ut_shopping', 'div_wt_sport', 'div_ut_sport', 'acc_care_other', 'acc_care_public', 'acc_school_superior', 'acc_school_basic', 'acc_leisure_ba

C:\Users\katul\AppData\Local\Temp\ipykernel_12728\855449977.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dft.drop(columns=DROP_COLS, inplace=True)
C:\Users\katul\AppData\Local\Temp\ipykernel_12728\855449977.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dft.rename(


In [4]:
lists_be = {
        'trip_purpose' : original_data['1500'].trip_purpose.unique(),
        'des_age_range' : original_data['1500'].des_age_range.unique(),
        'den_quartile' : original_data['1500'].den_quartile.unique()
        }

lists_dem = {
        'trip_purpose' : original_data['1500'].trip_purpose.unique(),
        'dem_cohort' : original_data['1500'].dem_cohort.unique(),
        'dem_hou_structure' : original_data['1500'].dem_hou_structure.unique()
        }

lists_with_be = {key: list(values) + ["all"] for key, values in lists_be.items()}
lists_with_dem = {key: list(values) + ["all"] for key, values in lists_dem.items()}

# Generate all combinations of the lists
combinations_be = product(*lists_with_be.values())
combinations_dem = product(*lists_with_dem.values())

# Build dictionaries for each combination
dict_combinations_be = [dict(zip(lists_with_be.keys(), combination)) for combination in combinations_be]
dict_combinations_dem = [dict(zip(lists_with_dem.keys(), combination)) for combination in combinations_dem]

control_combinations_be  = {"|".join([str(e) for e in di.values()]):di for di in dict_combinations_be}
control_combinations_dem  = {"|".join([str(e) for e in di.values()]):di for di in dict_combinations_dem}

In [5]:
control_combinations_be = {k:v for k,v in control_combinations_be.items() if not 'nan' in k and k.count('all') >= 1 }
control_combinations_dem = {k:v for k,v in control_combinations_dem.items() if not 'nan' in k and k.count('all') >= 1 }
CONTROL_COMBINATIONS = control_combinations_dem | control_combinations_be

In [6]:
CONTROL_COMBINATIONS

{'Shopping|More than 65|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'More than 65',
  'dem_hou_structure': 'all'},
 'Shopping|Ages 19-40|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Ages 19-40',
  'dem_hou_structure': 'all'},
 'Shopping|Ages 13-18|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Ages 13-18',
  'dem_hou_structure': 'all'},
 'Shopping|Ages 6-12|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Ages 6-12',
  'dem_hou_structure': 'all'},
 'Shopping|Ages 41-65|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Ages 41-65',
  'dem_hou_structure': 'all'},
 'Shopping|Less than 5|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Less than 5',
  'dem_hou_structure': 'all'},
 'Shopping|all|students_age13_18': {'trip_purpose': 'Shopping',
  'dem_cohort': 'all',
  'dem_hou_structure': 'students_age13_18'},
 'Shopping|all|retiree': {'trip_purpose': 'Shopping',
  'dem_cohort': 'all',
  'dem_hou_structure': 'retiree'},
 'Shopping|all|students_age6_12': {'trip_pur

In [7]:
dist_CONTROL_COMBINATIONS = {}
for k,v in CONTROL_COMBINATIONS.items():
    for d in ['900','1200','1500']:
        dist_CONTROL_COMBINATIONS.update({f"{d}|{k}":v})
        
CONTROL_COMBINATIONS = dist_CONTROL_COMBINATIONS

In [8]:
CONTROL_COMBINATIONS

{'900|Shopping|More than 65|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'More than 65',
  'dem_hou_structure': 'all'},
 '1200|Shopping|More than 65|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'More than 65',
  'dem_hou_structure': 'all'},
 '1500|Shopping|More than 65|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'More than 65',
  'dem_hou_structure': 'all'},
 '900|Shopping|Ages 19-40|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Ages 19-40',
  'dem_hou_structure': 'all'},
 '1200|Shopping|Ages 19-40|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Ages 19-40',
  'dem_hou_structure': 'all'},
 '1500|Shopping|Ages 19-40|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Ages 19-40',
  'dem_hou_structure': 'all'},
 '900|Shopping|Ages 13-18|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Ages 13-18',
  'dem_hou_structure': 'all'},
 '1200|Shopping|Ages 13-18|all': {'trip_purpose': 'Shopping',
  'dem_cohort': 'Ages 13-18',
  'dem_hou_structure': 'all'},
 '1500|

In [9]:
#for c in original_data['1500'].columns:
    #print(c)

In [10]:
SINGLE_VARIABLES = ['dem_income','dem_household_size','dem_gender','acc_transportation','den_pop_total','den_perc_unbuilt','den_perc_housing_sfr','des_mean_degree','des_straightness','des_betweenness', 'des_building_age']

In [11]:
# Define feature groups
FEATURE_GROUPS = {
    'acc_general': ['acc_care_other','acc_care_public', 'acc_school_superior', 'acc_school_basic','acc_leisure_bar', 'acc_leisure_cultural', 'acc_leisure_shows','acc_shopping_mall', 'acc_shopping_market', 'acc_shopping_alone','acc_sport_other'],
    'acc_green_areas' : ['acc_parks_S', 'acc_parks_M','acc_parks_L'],
    'den_urban_form' : ['den_far_ag','den_built_total'],
    'den_land_use_walkable' : ['den_perc_housing_ch', 'den_perc_care_other','den_perc_care_public', 'den_perc_school_superior','den_perc_school_basic', 'den_perc_leisure_bar','den_perc_leisure_cultural', 'den_perc_leisure_shows','den_perc_shopping_mall', 'den_perc_shopping_market','den_perc_shopping_alone', 'den_perc_sport_other', 'den_perc_office'],
    'den_less_walkable' : ['den_perc_industrial', 'den_perc_storage', 'den_perc_parking'],
    'div_walkable': ['div_wt_care','div_wt_school','div_wt_leisure','div_wt_shopping','div_wt_sport'],
    'div_unpaired': ['div_ut_care','div_ut_school','div_ut_leisure','div_ut_shopping','div_ut_sport'],
    'dem_attitude': ['dem_att_noprivate_dislike','dem_att_noprivate_hardtopark','dem_att_noprivate_lessconvenient','dem_att_noprivate_other','dem_att_noprivate_takeslonger','dem_att_noprivate_nan',
        'dem_att_nopublic_lessconvenient','dem_att_nopublic_other','dem_att_nopublic_preferactive','dem_att_nopublic_takeslonger','dem_att_nopublic_veryclose','dem_att_nopublic_nan',
        'dem_att_license','dem_att_vehicle','dem_att_card'],
    'dem_social': ['dem_education', 'dem_hou_size','dem_activity_retired','dem_activity_student',
        'dem_activity_unemployed','dem_activity_worker',
        'dem_hou_structure_children','dem_hou_structure_other',
        'dem_hou_structure_retiree','dem_hou_structure_students_age13_18',
        'dem_hou_structure_students_age6_12','dem_hou_structure_worker']} 

In [12]:
PURPOSE_VARIABLES = {
    'Shopping':['acc_shopping_mall','acc_shopping_market','acc_shopping_alone','den_perc_shopping_mall','den_perc_shopping_market','den_perc_shopping_alone','div_wt_shopping','div_ut_shopping'],
    'Study':['acc_school_superior','acc_school_basic','den_perc_school_superior','den_perc_school_basic','div_wt_school','div_ut_school'],
    'Leisure':['acc_leisure_bar','acc_leisure_cultural','acc_leisure_shows','den_perc_leisure_bar','den_perc_leisure_cultural','den_perc_leisure_shows','div_wt_leisure','div_ut_leisure'],
    'Sport / Stroll':['acc_sport_other', 'acc_parks_S', 'acc_parks_M', 'acc_parks_L','den_perc_sport_other'],
    'Care':['acc_care_other','acc_care_public', 'den_perc_care_other', 'den_perc_care_public','div_wt_care','div_ut_care',]}


In [13]:
COMBINATION_SCHEMA = []

In [14]:
import itertools

def merge_lists(list_of_lists):
    return list(itertools.chain.from_iterable(list_of_lists))


SCHEMA = {'pca_groups': None, 'single_variables': None, 'numeric_variables': None, 'categorical_variables': None, 'target_variable': None, 'control_variables': None}


def define_schemas(combination, filters):
    results = {}
    purpose = combination.split("|")[1]
    controls = [k for k,v in filters.items() if not v=='all']
    
    if controls ==  ['trip_purpose', 'dem_cohort'] or controls == ['trip_purpose', 'dem_hou_structure']:
        for schema in ['all_features_be', 'combined_features_be', 'purpose_combined_features_be','only_purpose_features_be','only_density','only_diversity','only_accessibility','only_design']:
            if schema == 'all_features_be':
                pca_groups = None
                single_variables = [d for d in SINGLE_VARIABLES if not "dem_" in d]
                numeric_variables = sorted(single_variables + merge_lists([[e for e in v if not e in single_variables] for k,v in FEATURE_GROUPS.items() if not k.startswith('dem')  and v])),
                results.update({schema:
                {
                'pca_groups': None,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
            elif schema == 'combined_features_be':
                pca_groups = {k:v for k,v in FEATURE_GROUPS.items() if not 'dem_' in k and v}
                single_variables = [d for d in SINGLE_VARIABLES if not "dem_" in d]
                numeric_variables = sorted(single_variables + list(pca_groups.keys()))
                results.update({schema:
                {
                'pca_groups': pca_groups,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
            elif schema == 'purpose_combined_features_be':
                pca_groups = {k:[d for d in v if d not in PURPOSE_VARIABLES[purpose]] for k,v in FEATURE_GROUPS.items() if not 'dem_' in k and v}
                single_variables = list(set([d for d in SINGLE_VARIABLES if not "dem_" in d] + PURPOSE_VARIABLES[purpose]))
                numeric_variables = sorted(single_variables + list(pca_groups.keys()))
                results.update({schema:
                {
                'pca_groups': pca_groups,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
            elif schema == 'only_purpose_features_be':
                pca_groups = None
                single_variables = list(set([d for d in SINGLE_VARIABLES if not "dem_" in d] + PURPOSE_VARIABLES[purpose]))
                numeric_variables = sorted(single_variables)
                results.update({schema:
                {
                'pca_groups': pca_groups,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
            elif schema == 'only_density':
                pca_groups = {k:[d for d in v if d not in PURPOSE_VARIABLES[purpose]] for k,v in FEATURE_GROUPS.items() if 'den_' in k and v}
                single_variables = list(set([d for d in SINGLE_VARIABLES if "den_" in d] + PURPOSE_VARIABLES[purpose]))
                numeric_variables = sorted(single_variables)
                results.update({schema:
                {
                'pca_groups': pca_groups,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
            elif schema == 'only_diversity':
                pca_groups = {k:[d for d in v if d not in PURPOSE_VARIABLES[purpose]] for k,v in FEATURE_GROUPS.items() if 'div_' in k and v}
                single_variables = list(set([d for d in SINGLE_VARIABLES if "div_" in d] + PURPOSE_VARIABLES[purpose]))
                numeric_variables = sorted(single_variables)
                results.update({schema:
                {
                'pca_groups': pca_groups,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
            elif schema == 'only_accessibility':
                pca_groups = {k:[d for d in v if d not in PURPOSE_VARIABLES[purpose]] for k,v in FEATURE_GROUPS.items() if 'acc_' in k and v}
                single_variables = list(set([d for d in SINGLE_VARIABLES if "acc_" in d] + PURPOSE_VARIABLES[purpose]))
                numeric_variables = sorted(single_variables)
                results.update({schema:
                {
                'pca_groups': pca_groups,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
            elif schema == 'only_design':
                pca_groups = {k:[d for d in v if d not in PURPOSE_VARIABLES[purpose]] for k,v in FEATURE_GROUPS.items() if 'des_' in k and v}
                single_variables = list(set([d for d in SINGLE_VARIABLES if "des_" in d] + PURPOSE_VARIABLES[purpose]))
                numeric_variables = sorted(single_variables)
                results.update({schema:
                {
                'pca_groups': pca_groups,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
    
    else:
        for schema in ['all_features_dem', 'combined_features_dem']:
            if schema == 'all_features_dem':
                pca_groups = None
                single_variables = [d for d in SINGLE_VARIABLES if  "dem_" in d]
                numeric_variables = sorted(single_variables + merge_lists([[e for e in v if not e in single_variables] for k,v in FEATURE_GROUPS.items() if k.startswith('dem')])),
                results.update({schema:
                {
                'pca_groups': None,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
            elif schema == 'combined_features_dem':
                pca_groups = {k:v for k,v in FEATURE_GROUPS.items() if  'dem_' in k and v}
                single_variables = [d for d in SINGLE_VARIABLES if  "dem_" in d]
                numeric_variables = sorted(single_variables + list(pca_groups.keys()))
                results.update({schema:
                {
                'pca_groups': pca_groups,
                'single_variables': single_variables,
                'numeric_variables':numeric_variables, 
                }})
         
    
    return results
 


In [15]:
RANDOM_STATE = 30
SAMPLE_THRESHOLD = 50000
TEST_SIZE = 0.3

In [16]:
import os
os.cpu_count()

8

In [17]:
class ModeClassifier:
    
    def __init__(self, dataset, schema, control_combination, grid_search = False):
        """
        Initialize the ModeClassifier class.

        Parameters:
        - dataset: Input dataset (pandas DataFrame).
        - schema: A dictionary with PCA groupings and single variables.
        - control_combinations: A dictionary of combinations for filtering the dataset.
        """
        self.original_dataset = dataset
        self.filtered_dataset = None
        self.schema = schema
        self.control_combinations = control_combination
        self.results = {}
        self.plots = None
        self.discard = False
        self.grid_search = grid_search

    def prepare_rows(self):

        filtered_data = self.original_dataset.copy()
        logger.info(f"Length of original dataset is {str(len(filtered_data))}")
        for key, value in self.control_combinations.items():
            if value != "all":
                filtered_data = filtered_data[filtered_data[key] == value]
        
        logger.info(f"Length of filtered dataset is {str(len(filtered_data))}")
        logger.info(f"Sample Size of filtered dataset is {str(int(filtered_data['elevator'].sum()))}")
        
        if filtered_data['elevator'].sum() < SAMPLE_THRESHOLD:
            
            logger.opt(colors=True).info(f"<r>Model is discarded for being too a little sample</r>")
            self.discard = True
        else:
            self.filtered_dataset = filtered_data
    
    def prepare_columns(self):
        
        def prepare_schema():
            columns = []
            for sch in self.schema.values():
                if not sch:
                    pass
                elif isinstance(sch,tuple): columns.append(sch[0])
                elif isinstance(sch,list): columns.append(sch)
                elif isinstance(sch,str): columns.append([sch])
            l = merge_lists(columns)
            return  sorted(list(set(l))) #Do something better than hardcoding this here
        
        if self.schema['pca_groups']:
            self.apply_pca()
            cols = prepare_schema()+['elevator','trip_mode']
            self.filtered_dataset = self.filtered_dataset[[c for c in cols if c in self.filtered_dataset.columns]]
            #print(self.filtered_dataset.head(5).to_string())
            logger.info(f"Final schema is {", ".join(cols)}")
        else: 
            cols = prepare_schema()+['elevator','trip_mode']
            self.filtered_dataset = self.filtered_dataset[[c for c in cols if c in self.filtered_dataset.columns]]
            #print(self.filtered_dataset.head(5).to_string())
            logger.info(f"Final schema is {", ".join(cols)}")
            
    def split_sample_data(self, test_size = TEST_SIZE, random_state = RANDOM_STATE):
        """
        Filter the dataset based on the provided combination and prepare feature sets.
        """

        # Split data
        X = self.filtered_dataset.drop(columns=['trip_mode'])  # Adjust as needed
        y = self.filtered_dataset['trip_mode']
        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=test_size, random_state=random_state)

        undersampler = RandomUnderSampler(random_state=random_state)
        X_train, y_train = undersampler.fit_resample(X_train, y_train)
        logger.info(f"Final size after undersampling is {str(len(X_train))}")
        return X_train, X_test, y_train, y_test
    
    def apply_pca(self):
        """
        Apply PCA to grouped features defined in the schema.
        """    
        
        for group_name, features in self.schema['pca_groups'].items():
            if len(features) != 0:
                pca = PCA(n_components=1)
                self.filtered_dataset[group_name] = pca.fit_transform(self.filtered_dataset[features])
        
        merged_columns = merge_lists(self.schema['pca_groups'].values())
        
        self.filtered_dataset.drop(columns= merged_columns, inplace=True)
        
    def train_model(self, model, X_train, y_train, X_test, y_test, model_name):
        """
        Train a model and compute accuracy.
        """
        if not self.grid_search:
            weights = X_train['elevator'].values
            X_train = X_train.drop(columns=['elevator'])
            X_test = X_test.drop(columns=['elevator'])
            model.fit(X_train, y_train, sample_weight = weights)
            y_pred = model.predict(X_test)
            accuracy = round(accuracy_score(y_test, y_pred),3)
            logger.info(f"Accuracy of {model_name} is {str(accuracy)}")
            return model, accuracy, None
        
        else:
            if model_name == 'Binomial Logistic Regression':
                param_grid = {
                    'C': [0.01, 10],
                    'penalty': ['l2'],  
                    'solver': ['lbfgs']}
            elif model_name == 'Random Forest':
                param_grid = {
                    'n_estimators': [100, 300],
                    'max_depth': [None, 10],
                    'min_samples_split': [2, 10],
                    #'min_samples_leaf': [1, 2, 4]
                    }
            
            grid_search = GridSearchCV(
                estimator=model,
                param_grid=param_grid,
                scoring="accuracy",
                cv=3,
                verbose=1,
                n_jobs=7,
            )

            weights = X_train['elevator'].values
            X_train = X_train.drop(columns=['elevator'])
            X_test = X_test.drop(columns=['elevator'])

            grid_search.fit(X_train, y_train, sample_weight=weights)
            best_model = grid_search.best_estimator_
            best_params = grid_search.best_params_

            y_pred = best_model.predict(X_test)
            accuracy = round(accuracy_score(y_test, y_pred), 3)

            logger.info(f"Accuracy of {model_name} is {str(accuracy)}")
            return best_model, accuracy, best_params
    
    def process_combination(self):
        """
        Process the instance's combination, schema, and models
        """
        logger.opt(colors=True).info(f"<e>Prepare Rows</e>")
        self.prepare_rows()
        if self.discard: return
        logger.opt(colors=True).info(f"<e>Prepare Columns</e>")
        self.prepare_columns()
        if self.discard: return
        logger.opt(colors=True).info(f"<e>Split Sample Data</e>")

        X_train, X_test, y_train, y_test = self.split_sample_data()
        
        logger.opt(colors=True).info(f"<e>Train Random Forest</e>")
        
        rf, rf_acc, best_rf = self.train_model(
        RandomForestClassifier(random_state=RANDOM_STATE),
        X_train, y_train, X_test, y_test, "Random Forest")
        
        logger.opt(colors=True).info(f"<e>Train Logistic Regression</e>")
        
        mlr, mlr_acc, best_mlr = self.train_model(
            LogisticRegression(solver='lbfgs', max_iter=1000, random_state=RANDOM_STATE),
            X_train, y_train, X_test, y_test, "Binomial Logistic Regression"
        )

        self.results = {
            'rf_model': rf,
            'rf_accuracy': rf_acc,
            'mlr_model': mlr,
            'mlr_accuracy': mlr_acc,
            'rf_importance': pd.Series(rf.feature_importances_, index=X_train.drop(columns='elevator').columns).sort_values(ascending=False),
            'mlr_coefficients': pd.DataFrame(mlr.coef_,columns=X_train.drop(columns='elevator').columns,index=[f"{mlr.classes_[1]} vs {mlr.classes_[0]}"]),
            'X_train': X_train.drop(columns='elevator'),
            'y_train': y_train,
            'X_test': X_test.drop(columns='elevator'),
            'y_test': y_test}
  
    def plot_confusion_matrix(self, y_true, y_pred, title="Confusion Matrix", cmap="Blues"):
        """Plot a confusion matrix."""
        cm = confusion_matrix(y_true, y_pred)
        plt.figure(figsize=(8, 6))
        sns.heatmap(cm, annot=True, fmt="d", cmap=cmap, xticklabels=["Walking", "Motor"], yticklabels=["Walking", "Motor"])
        plt.title(title)
        plt.xlabel("Predicted")
        plt.ylabel("Actual")
        plt.show()


In [18]:
age = ['More than 65', 'Ages 41-65', 'Ages 13-18', 'Ages 6-12','Ages 19-40']
building_age = ['1960-1980', '1980-2000', '2000-2010', '1930-1960']
activity = ['retiree', 'worker', 'other', 'students_age13_18','students_age6_12','age19m']
density = ['den_hou_Q3', 'den_hou_Q2','den_hou_Q4', 'den_hou_Q1']
be_schemas = ['all_features_be', 'combined_features_be','purpose_combined_features_be', 'only_purpose_features_be','only_density', 'only_diversity', 'only_accessibility''only_design']
dem_schemas =  ['all_features_dem', 'combined_features_dem']

In [19]:
def is_valid_combination(combination: str, schema: str) -> bool:
    """
    Checks if a given combination string and schema name are valid based on rules.

    """
    # Lists of keywords for various categories
    age = ['More than 65', 'Ages 41-65', 'Ages 13-18', 'Ages 6-12', 'Ages 19-40','Less than 5']
    activity = ['retiree', 'worker', 'other', 'students_age13_18', 'students_age6_12', 'age19m', 'children']
    building_age = ['1960-1980', '1980-2000', '2000-2010', '1930-1960','1880-1930']
    density = ['den_hou_Q3', 'den_hou_Q2', 'den_hou_Q4', 'den_hou_Q1']
    be_schemas = ['all_features_be', 'combined_features_be', 'purpose_combined_features_be', 
                  'only_purpose_features_be', 'only_density', 'only_diversity', 
                  'only_accessibility', 'only_design']
    dem_schemas = ['all_features_dem', 'combined_features_dem']

    # Split the combination string
    parts = combination.split('|')
    if len(parts) < 4:
        raise ValueError(f"Invalid combination format: {combination}")

    # Extract positions from the combination
    third_position = parts[2]
    fourth_position = parts[3]

    # Rule 1: Demographic combinations
    if third_position in age or fourth_position in activity:
        return schema in be_schemas

    # Rule 2: Built environment combinations
    if third_position in building_age or fourth_position in density:
        return schema in dem_schemas

    # Rule 3: 'all' in both third and fourth positions
    if third_position == 'all' and fourth_position == 'all':
        return schema in be_schemas + dem_schemas

    # If none of the rules match, the combination is invalid
    return False


In [20]:
PROCESSED_COMBINATIONS = {}
for k,v in CONTROL_COMBINATIONS.items():
    logger.opt(colors=True).info(f"<m>Processing combination {k}</m>")
    data = original_data[k.split('|')[0]]
    schemas = define_schemas(k, v)
    for a,s in list(schemas.items()):
        if is_valid_combination(k, a):
            logger.opt(colors=True).info(f"<y>Processing schema {a}</y>")
            instance = ModeClassifier(data, s, v, grid_search=True)
            try:
                instance.process_combination()
            except Exception as e:
                print(f"Model failed for {k} {a}: {e}")
            PROCESSED_COMBINATIONS.update({f"{k}|{a}": instance})    
        

2024-12-08 11:33:26.844 | INFO     | __main__:<module>:3 - Processing combination 900|Shopping|More than 65|all
2024-12-08 11:33:26.845 | INFO     | __main__:<module>:8 - Processing schema all_features_be
2024-12-08 11:33:26.845 | INFO     | __main__:process_combination:148 - Prepare Rows
2024-12-08 11:33:26.858 | INFO     | __main__:prepare_rows:24 - Length of original dataset is 17540
2024-12-08 11:33:26.867 | INFO     | __main__:prepare_rows:29 - Length of filtered dataset is 1617
2024-12-08 11:33:26.868 | INFO     | __main__:prepare_rows:30 - Sample Size of filtered dataset is 117749
2024-12-08 11:33:26.869 | INFO     | __main__:process_combination:151 - Prepare Columns
2024-12-08 11:33:26.870 | INFO     | __main__:prepare_columns:62 - Final schema is acc_care_other, acc_care_public, acc_leisure_bar, acc_leisure_cultural, acc_leisure_shows, acc_parks_L, acc_parks_M, acc_parks_S, acc_school_basic, acc_school_superior, acc_shopping_alone, acc_shopping_mall, acc_shopping_market, acc_s

Fitting 3 folds for each of 8 candidates, totalling 24 fits


2024-12-08 11:33:31.187 | INFO     | __main__:train_model:141 - Accuracy of Random Forest is 0.671
2024-12-08 11:33:31.188 | INFO     | __main__:process_combination:164 - Train Logistic Regression
2024-12-08 11:33:31.234 | INFO     | __main__:train_model:141 - Accuracy of Binomial Logistic Regression is 0.617
2024-12-08 11:33:31.242 | INFO     | __main__:<module>:8 - Processing schema combined_features_be
2024-12-08 11:33:31.242 | INFO     | __main__:process_combination:148 - Prepare Rows
2024-12-08 11:33:31.259 | INFO     | __main__:prepare_rows:24 - Length of original dataset is 17540
2024-12-08 11:33:31.268 | INFO     | __main__:prepare_rows:29 - Length of filtered dataset is 1617
2024-12-08 11:33:31.271 | INFO     | __main__:prepare_rows:30 - Sample Size of filtered dataset is 117749
2024-12-08 11:33:31.272 | INFO     | __main__:process_combination:151 - Prepare Columns
2024-12-08 11:33:31.294 | INFO     | __main__:prepare_columns:57 - Final schema is acc_general, acc_green_areas, 

Fitting 3 folds for each of 2 candidates, totalling 6 fits
Fitting 3 folds for each of 8 candidates, totalling 24 fits


2024-12-08 11:33:33.017 | INFO     | __main__:train_model:141 - Accuracy of Random Forest is 0.617
2024-12-08 11:33:33.018 | INFO     | __main__:process_combination:164 - Train Logistic Regression
2024-12-08 11:33:33.052 | INFO     | __main__:train_model:141 - Accuracy of Binomial Logistic Regression is 0.603
2024-12-08 11:33:33.068 | INFO     | __main__:<module>:8 - Processing schema purpose_combined_features_be
2024-12-08 11:33:33.069 | INFO     | __main__:process_combination:148 - Prepare Rows
2024-12-08 11:33:33.080 | INFO     | __main__:prepare_rows:24 - Length of original dataset is 17540
2024-12-08 11:33:33.093 | INFO     | __main__:prepare_rows:29 - Length of filtered dataset is 1617
2024-12-08 11:33:33.094 | INFO     | __main__:prepare_rows:30 - Sample Size of filtered dataset is 117749
2024-12-08 11:33:33.095 | INFO     | __main__:process_combination:151 - Prepare Columns
2024-12-08 11:33:33.116 | INFO     | __main__:prepare_columns:57 - Final schema is acc_general, acc_green

...

Fitting 3 folds for each of 2 candidates, totalling 6 fits
Fitting 3 folds for each of 8 candidates, totalling 24 fits


2024-12-08 12:10:18.793 | INFO     | __main__:train_model:141 - Accuracy of Random Forest is 0.884
2024-12-08 12:10:18.794 | INFO     | __main__:process_combination:164 - Train Logistic Regression
2024-12-08 12:10:18.854 | INFO     | __main__:train_model:141 - Accuracy of Binomial Logistic Regression is 0.868
2024-12-08 12:10:18.862 | INFO     | __main__:<module>:8 - Processing schema combined_features_dem
2024-12-08 12:10:18.863 | INFO     | __main__:process_combination:148 - Prepare Rows
2024-12-08 12:10:18.882 | INFO     | __main__:prepare_rows:24 - Length of original dataset is 21837
2024-12-08 12:10:18.889 | INFO     | __main__:prepare_rows:29 - Length of filtered dataset is 5535
2024-12-08 12:10:18.890 | INFO     | __main__:prepare_rows:30 - Sample Size of filtered dataset is 420612
2024-12-08 12:10:18.891 | INFO     | __main__:process_combination:151 - Prepare Columns
2024-12-08 12:10:18.899 | INFO     | __main__:prepare_columns:57 - Final schema is dem_attitude, dem_gender, dem

Fitting 3 folds for each of 2 candidates, totalling 6 fits
Fitting 3 folds for each of 8 candidates, totalling 24 fits


2024-12-08 12:10:21.736 | INFO     | __main__:train_model:141 - Accuracy of Random Forest is 0.889
2024-12-08 12:10:21.738 | INFO     | __main__:process_combination:164 - Train Logistic Regression
2024-12-08 12:10:21.770 | INFO     | __main__:train_model:141 - Accuracy of Binomial Logistic Regression is 0.578


Fitting 3 folds for each of 2 candidates, totalling 6 fits


In [21]:
results_df = {
'table_size': {name: len(model.filtered_dataset) for name, model in PROCESSED_COMBINATIONS.items() if model.discard is False},
'sample_size': {name: round(model.filtered_dataset['elevator'].sum(),0) for name, model in PROCESSED_COMBINATIONS.items() if model.discard is False},
'rf_accuracy' : {name: model.results['rf_accuracy'] for name, model in PROCESSED_COMBINATIONS.items() if model.discard is False},
'mlr_accuracy' : {name: model.results['mlr_accuracy'] for name, model in PROCESSED_COMBINATIONS.items() if model.discard is False},
'discarded' : {name: model.discard for name, model in PROCESSED_COMBINATIONS.items() if model.discard is False}
}
results_df = pd.DataFrame(results_df)
results_df['distance_threshold'] = results_df.index.str.split("|").str[0]
results_df['trip_purpose'] = results_df.index.str.split("|").str[1]
results_df['age_cohort'] = results_df.index.str.split("|").str[2]
results_df['activity_cohort'] = results_df.index.str.split("|").str[3]
results_df['schema'] = results_df.index.str.split("|").str[4]


In [22]:
results_df['age_cohort'].unique()

array(['More than 65', 'Ages 41-65', 'all', 'Ages 13-18', 'Ages 6-12',
       'Ages 19-40', '1960-1980', '1980-2000', '2000-2010', '1930-1960'],
      dtype=object)

In [23]:
results_df = pd.concat([results_df[(results_df['schema'].str.endswith("dem"))&(results_df['age_cohort'] == 'all')&(results_df['activity_cohort'] == 'all')],
results_df[(results_df['schema'].str.endswith("dem"))&(results_df['age_cohort'].isin(building_age))&(results_df['activity_cohort'] == 'all')],
results_df[(results_df['schema'].str.endswith("dem"))&(results_df['activity_cohort'].isin(density))&(results_df['age_cohort'] == 'all')],
results_df[(results_df['schema'].isin(be_schemas))&(results_df['activity_cohort'].isin(activity))&(results_df['age_cohort'] == 'all')],
results_df[(results_df['schema'].isin(be_schemas))&(results_df['activity_cohort'] == 'all')&(results_df['age_cohort'].isin(age))]])

In [24]:
print(results_df[(results_df['distance_threshold'] == '1500')].sort_values(by='rf_accuracy',ascending=False).to_string())

                                                                   table_size  sample_size  rf_accuracy  mlr_accuracy  discarded distance_threshold    trip_purpose    age_cohort    activity_cohort                        schema
1500|Care|all|den_hou_Q4|all_features_dem                                 726      54359.0        0.982         0.977      False               1500            Care           all         den_hou_Q4              all_features_dem
1500|Shopping|1960-1980|all|all_features_dem                             1712     126158.0        0.979         0.922      False               1500        Shopping     1960-1980                all              all_features_dem
1500|Care|all|all|all_features_dem                                       3728     262902.0        0.978         0.973      False               1500            Care           all                all              all_features_dem
1500|Care|1980-2000|all|all_features_dem                                 2213     155578.0  

In [ ]:
print(results_df[(results_df['distance_threshold'] == '1500')&(results_df.index.str[-3:]!='dem') & () & ()].sort_values(by='rf_accuracy',ascending=False).to_string())

                                                                   table_size  sample_size  rf_accuracy  mlr_accuracy  discarded distance_threshold    trip_purpose    age_cohort    activity_cohort                        schema
1500|Sport / Stroll|More than 65|all|only_purpose_features_be            2103     149727.0        0.777         0.737      False               1500  Sport / Stroll  More than 65                all      only_purpose_features_be
1500|Sport / Stroll|More than 65|all|purpose_combined_features_be        2103     149727.0        0.770         0.773      False               1500  Sport / Stroll  More than 65                all  purpose_combined_features_be
1500|Sport / Stroll|More than 65|all|combined_features_be                2103     149727.0        0.765         0.834      False               1500  Sport / Stroll  More than 65                all          combined_features_be
1500|Sport / Stroll|More than 65|all|all_features_be                     2103     149727.0  

In [ ]:
q = [c for c in q if not c in ['dens_far', 'dens_pop_total','des_total_length','dem_population_18','dem_population_65','den_perc_hotel','des_closeness','des_eigenvector']]

In [ ]:
plt.figure(figsize=(40, 40))
sns.heatmap(data['300'][q].corr(), annot=True, cmap='coolwarm', fmt='.2f')
plt.title("Feature Correlation Matrix")
plt.show()

In [ ]:
plt.figure(figsize=(40, 40))
sns.heatmap(data['600'][q].corr(), annot=True, cmap='coolwarm', fmt='.2f')
plt.title("Feature Correlation Matrix")
plt.show()

In [ ]:
plt.figure(figsize=(8.5, 11))
sns.heatmap(data['900'][q].corr(), annot=False, cmap='coolwarm', fmt='.2f')
plt.title("Feature Correlation Matrix")
plt.show()